# KLF beamline simulation results, take 6 (GlueX Phase 2 beamline)
This is a sixth simulation of the Hall D beamline for the KLF experiment, this time under quite different conditions. Instead of the CPS photon source and the KPT conversion target, the standard GlueX photon beam configuration is used: diamond radiator at the standard goniometer position, and the standard Hall D alcove configuration used by GlueX with a 5mm diameter collimator, two sweeping magnets, the pair spectrometer and the shielding wall just upstream of the GlueX liquid hydrogen target. The purpose of this simulation is to provide a baseline of hit rates in the GlueX detectors under known detector operating and triggering conditions, particularly in the start counter, the drift chambes, and the tof counter. This should provide a quantitative basis for evaluation of the rates predicted by the simulation of the klong beam in the CPS + KPT configuration. 

Plot summed results from simulation of 250M simulated beam photons in the range [0.0001,12] GeV from a 50um diamond radiator passing through the 5mm collimator in the Hall D alcove. This simulation subtends approximately 22 milliseconds of beam at 350nA electron beam intensity at 12GeV endpoint energy.

In [1]:
import ROOT
%jsroot on
import os
os.chdir("/srv/jupyter/hdgeant4 studies")
import pyxrootd.client as xclient
import numpy as np
#%pip install --user "gluex.jupyroot>=1.0.10"
from gluex.jupyroot.treeview import treeview

In [2]:
import dask.distributed
import dask
dclient = dask.distributed.Client(n_workers=50, threads_per_worker=1, dashboard_address='0.0.0.0:8790')

/srv/.local/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 8790 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 33205 instead
  warnings.warn(


In [3]:
mass_proton = 0.93827208943 # GeV/c^2
mass_neutron = 0.93956542194 # GeV/c^2
mass_klong = 0.497611 # GeV/c^2
mass_muon = 0.10566 # GeV/c^2
mass_electron = 5.11e-3
mass_deuteron = mass_proton + mass_neutron - 2.2e-3 # GeV/c^2

In [4]:
xrdurl = "root://cn445.storrs.hpc.uconn.edu"
xrdpath = "/Gluex/resilient/simulation/KLFbeam-8-2024/"
rfile1 = ROOT.TFile.Open(xrdurl + xrdpath + "bgprofiles6_1.root")
chains = {}
for tree in rfile1.GetListOfKeys():
    chains[tree.GetName()] = ROOT.TChain(tree.GetName(), tree.GetTitle())
    print("created new chain for", tree.GetName())

created new chain for det1
created new chain for det2
created new chain for det3
created new chain for det5
created new chain for det6
created new chain for det7


In [5]:
xfs = xclient.FileSystem(xrdurl)
chdet57 = ROOT.TChain()
for f in xfs.dirlist(xrdpath)[1]['dirlist'][:100000]:
    if "bgprofiles6_" in f['name']:
        for chain in chains:
            chains[chain].Add(xrdurl + xrdpath + f['name'])
            if chain == 'det5' or chain == 'det7':
                chdet57.Add(xrdurl + xrdpath + f['name'] + f"?#{chain}")
chains['det5+det7'] = chdet57
for chain in chains:
    print("chain", chain, "created with", chains[chain].GetNtrees(), "files")

chain det1 created with 1186 files
chain det2 created with 1186 files
chain det3 created with 1186 files
chain det5 created with 1186 files
chain det6 created with 1186 files
chain det7 created with 1186 files
chain det5+det7 created with 2372 files


In [6]:
tview = treeview(chains['det5+det7'], "Klong_beam6.root/det5")
tview.enable_dask_cluster(dclient)

## Particles at the entrance to the GlueX liquid hydrogen target

In [7]:
def det5_ptype_hinit():
    h = {}
    h['hptypef'] = ROOT.TH1D('hptypef', "particle type at GlueX entrance plane", 100, 0, 100)
    h['hptypef'].GetXaxis().SetTitle("Geant particle type")
    h['hptypef'].GetYaxis().SetTitle("counts")
    return h

def det5_ptype_hfill(row, histos):
    if row.x[5] > 0:
        histos['hptypef'].Fill(row.ptype)
    return histos

n = tview.declare_histograms("particle type", det5_ptype_hinit, det5_ptype_hfill)

In [8]:
#tview.fill_histograms()
n = tview.draw('hptypef', width=600)

In [9]:
def det5_klong_hinit():
    h = {}
    h['hklfspot'] = ROOT.TH2D("hklfspot", "klong impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['hklfspot'].GetXaxis().SetTitle("impact x (cm)")
    h['hklfspot'].GetYaxis().SetTitle("impact y (cm)")
    h['hklfspot2'] = ROOT.TH2D("hklfspot2", "klong impact point at GlueX entrance plane", 100, -10, 10, 100, -10, 10)
    h['hklfspot2'].GetXaxis().SetTitle("impact x (cm)")
    h['hklfspot2'].GetYaxis().SetTitle("impact y (cm)")
    h['hklftotE'] = ROOT.TH1D('hklftotE', "klong total energy inside pipe at GlueX entrance plane", 120, 0, 12)
    h['hklftotE'].GetXaxis().SetTitle("klong total energy (GeV)")
    h['hklftotE'].GetYaxis().SetTitle("counts")
    h['hklfmom'] = ROOT.TH1D('hklfmom', "klong momentum inside pipe at GlueX entrance plane", 120, 0, 12)
    h['hklfmom'].GetXaxis().SetTitle("klong momentum (GeV/c)")
    h['hklfmom'].GetYaxis().SetTitle("counts")
    return h

def det5_klong_hfill(row, histos):
    if row.ptype == 10 and row.x[5] > 0:
        histos['hklfspot'].Fill(row.x[0], row.x[1])
        histos['hklfspot2'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['hklftotE'].Fill(row.totE)
            histos['hklfmom'].Fill((row.totE**2 - mass_klong**2)**0.5)
    return histos

n = tview.declare_histograms("forward klong at det5", det5_klong_hinit, det5_klong_hfill)

In [10]:
#tview.fill_histograms()
n = tview.draw([['hklfspot', 'hklfspot2'], ['hklftotE', 'hklfmom']],
               [['colz', 'colz'], ['', '']])

In [11]:
def det5_gamma_hinit():
    h = {}
    h['hgamfspot'] = ROOT.TH2D('hgamfspot', "gamma impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['hgamfspot'].GetXaxis().SetTitle("impact x (cm)")
    h['hgamfspot'].GetYaxis().SetTitle("impact y (cm)")
    h['hgamfspot2'] = ROOT.TH2D('hgamfspot2', "gamma impact point at GlueX entrance plane", 200, -10, 10, 200, -10, 10)
    h['hgamfspot2'].GetXaxis().SetTitle("impact x (cm)")
    h['hgamfspot2'].GetYaxis().SetTitle("impact y (cm)")
    h['hgamftotE'] = ROOT.TH1D('hgamftotE', "gamma total energy inside pipe at GlueX entrance plane", 500, -5, 1)
    h['hgamftotE'].GetXaxis().SetTitle("log10(gamma energy / GeV)")
    h['hgamftotE'].GetYaxis().SetTitle("counts")
    for i in range(4):
        h[f'hgamftotE{i}'] = ROOT.TH1D(f'hgamftotE{i}', "gamma total energy inside pipe at GlueX entrance plane", 500, -5, 1)
        h[f'hgamftotE{i}'].GetXaxis().SetTitle("log10(gamma energy / GeV)")
        h[f'hgamftotE{i}'].GetYaxis().SetTitle("counts")
    return h

def det5_gamma_hfill(row, histos):
    if row.ptype == 1 and row.x[5] > 0:
        histos['hgamfspot'].Fill(row.x[0], row.x[1])
        histos['hgamfspot2'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['hgamftotE'].Fill(np.log10(row.totE))
            if row.run <= 122500:
                histos['hgamftotE0'].Fill(np.log10(row.totE))
            elif row.run <= 125000:
                histos['hgamftotE1'].Fill(np.log10(row.totE))
            elif row.run <= 127500:
                histos['hgamftotE2'].Fill(np.log10(row.totE))
            else:
                histos['hgamftotE3'].Fill(np.log10(row.totE))
    return histos

n = tview.declare_histograms("forward gamma at det5", det5_gamma_hinit, det5_gamma_hfill)

In [12]:
#tview.fill_histograms()
n = tview.draw(['hgamfspot2', 'hgamftotE'], ['colz', ''])

In [13]:
def det5_neutron_hinit():
    h = {}
    h['hneufspot'] = ROOT.TH2D('hneufspot', "neutron impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['hneufspot'].GetXaxis().SetTitle("impact x (cm)")
    h['hneufspot'].GetYaxis().SetTitle("impact y (cm)")
    h['hneufspot2'] = ROOT.TH2D('hneufspot2', "neutron impact point at GlueX entrance plane", 100, -10, 10, 100, -10, 10)
    h['hneufspot2'].GetXaxis().SetTitle("impact x (cm)")
    h['hneufspot2'].GetYaxis().SetTitle("impact y (cm)")
    h['hneufkinE'] = ROOT.TH1D('hneufkinE', "neutron kinetic energy inside pipe at GlueX entrance plane", 500, -5, 1)
    h['hneufkinE'].GetXaxis().SetTitle("log10(neutron kinetic energy / GeV)")
    h['hneufkinE'].GetYaxis().SetTitle("counts")
    return h

def det5_neutron_hfill(row, histos):
    if row.ptype==13 and row.x[5] > 0:
        histos['hneufspot'].Fill(row.x[0], row.x[1])
        histos['hneufspot2'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['hneufkinE'].Fill(np.log10(row.totE - mass_neutron)) 

n = tview.declare_histograms("forward neutrons at det5", det5_neutron_hinit, det5_neutron_hfill)

In [14]:
#tview.fill_histograms()
n = tview.draw(['hneufspot', 'hneufkinE'], ['colz', ''])

In [15]:
hneufkinE = tview.get('hneufkinE')
print(hneufkinE.Integral(hneufkinE.GetXaxis().FindBin(-1), 500))

0.0


In [16]:
def det5_proton_hinit():
    h = {}
    h['hprofspot'] = ROOT.TH2D('hprofspot', "proton impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['hprofspot'].GetXaxis().SetTitle("impact x (cm)")
    h['hprofspot'].GetYaxis().SetTitle("impact y (cm)")
    h['hprofkinE'] = ROOT.TH1D('hprofkinE', "proton kinetic energy inside pipe at GlueX entrance plane", 500, -5, 1)
    h['hprofkinE'].GetXaxis().SetTitle("log10(proton kinetic energy / GeV)")
    h['hprofkinE'].GetYaxis().SetTitle("counts")
    return h

def det5_proton_hfill(row, histos):
    if row.ptype == 14 and row.x[5] > 0:
        histos['hprofspot'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['hprofkinE'].Fill(np.log10(row.totE - mass_proton))
    return histos

n = tview.declare_histograms("forward protons at det5", det5_proton_hinit, det5_proton_hfill)

In [17]:
#tview.fill_histograms()
n = tview.draw(['hprofspot', 'hprofkinE'], ['colz', ''])

In [18]:
def det5_nuclei_hinit():
    h = {}
    h['hdeufspot'] = ROOT.TH2D('hdeufspot', "deuteron impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['hdeufspot'].GetXaxis().SetTitle("impact x (cm)")
    h['hdeufspot'].GetYaxis().SetTitle("impact y (cm)")
    h['hdeufkinE'] = ROOT.TH1D('hdeufkinE', "deuteron kinetic energy inside pipe at GlueX entrance plane", 500, -5, 1)
    h['hdeufkinE'].GetXaxis().SetTitle("log10(deuteron kinetic energy / GeV)")
    h['hdeufkinE'].GetYaxis().SetTitle("counts")
    return h

def det5_nuclei_hfill(row, histos):
    if row.ptype == 45 and row.x[5] > 0:
        histos['hdeufspot'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['hdeufkinE'].Fill(np.log10(row.totE - mass_deuteron))
    return histos

n = tview.declare_histograms("forward nuclei at det5", det5_nuclei_hinit, det5_nuclei_hfill)

In [19]:
#tview.fill_histograms()
n = tview.draw(['hdeufspot', 'hdeufkinE'], ['colz', ''])

In [20]:
def det5_muons_hinit():
    h = {}
    h['hmufspot'] = ROOT.TH2D('hmufspot', "muon impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['hmufspot'].GetXaxis().SetTitle("impact x (cm)")
    h['hmufspot'].GetYaxis().SetTitle("impact y (cm)")
    h['hmufkinE'] = ROOT.TH1D('hmufkinE', "muon kinetic energy inside pipe at GlueX entrance plane", 500, -5, 1)
    h['hmufkinE'].GetXaxis().SetTitle("log10(muon kinetic energy / GeV)")
    h['hmufkinE'].GetYaxis().SetTitle("counts")
    return h

def det5_muons_hfill(row, histos):
    if (row.ptype == 5 or row.ptype == 6) and row.x[5] > 0:
        histos['hmufspot'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['hmufkinE'].Fill(np.log10(row.totE - mass_muon))
    return histos

n = tview.declare_histograms("forward muons at det5", det5_muons_hinit, det5_muons_hfill)

In [21]:
#tview.fill_histograms()
n = tview.draw(['hmufspot', 'hmufkinE'], ['colz', ''])

In [22]:
def det5_electron_hinit():
    h = {}
    h['helefspot'] = ROOT.TH2D('helefspot', "e+/e- impact point at GlueX entrance plane", 600, -300, 300, 600, -300, 300)
    h['helefspot'].GetXaxis().SetTitle("impact x (cm)")
    h['helefspot'].GetYaxis().SetTitle("impact y (cm)")
    h['helefkinE'] = ROOT.TH1D('helefkinE', "e+/e- kinetic energy inside pipe at GlueX entrance plane", 500, -5, 1)
    h['helefkinE'].GetXaxis().SetTitle("log10(electron kinetic energy / GeV)")
    h['helefkinE'].GetYaxis().SetTitle("counts")
    return h

def det5_electron_hfill(row, histos):
    if (row.ptype == 2 or row.ptype == 3) and row.x[5] > 0:
        histos['helefspot'].Fill(row.x[0], row.x[1])
        if row.x[0]**2 + row.x[1]**2 < 9:
            histos['helefkinE'].Fill(np.log10(row.totE - mass_electron))
    return histos

n = tview.declare_histograms("forward electrons at det5", det5_electron_hinit, det5_electron_hfill)

In [23]:
#tview.fill_histograms()
n = tview.draw(['helefspot', 'helefkinE'], ['colz', ''])

In [24]:
h = tview.get('helefkinE')
h.Integral(h.GetXaxis().FindBin(np.log10(0.5)), 500)

16.0

The contents of the bgprofiles det5 tree are as follows.

    ******************************************************************************
    *Tree    :det7      : hits in virtual detector 7                             *
    *Entries :    38579 : Total =         3875944 bytes  File  Size =    2063721 *
    *        :          : Tree compression factor =   1.88                       *
    ******************************************************************************
    *Br    0 :run       : run/I                                                  *
    *Entries :    38579 : Total  Size=     155143 bytes  File Size  =       1295 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression= 119.43     *
    *............................................................................*
    *Br    1 :event     : event/I                                                *
    *Entries :    38579 : Total  Size=     155161 bytes  File Size  =      67165 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression=   2.30     *
    *............................................................................*
    *Br    2 :totE      : totE/F                                                 *
    *Entries :    38579 : Total  Size=     155152 bytes  File Size  =     140862 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression=   1.10     *
    *............................................................................*
    *Br    3 :time      : time/F                                                 *
    *Entries :    38579 : Total  Size=     155152 bytes  File Size  =      42327 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression=   3.65     *
    *............................................................................*
    *Br    4 :x         : x[7]/F                                                 *
    *Entries :    38579 : Total  Size=    1083499 bytes  File Size  =     831599 *
    *Baskets :       34 : Basket Size=      32000 bytes  Compression=   1.30     *
    *............................................................................*
    *Br    5 :ppol      : ppol/F                                                 *
    *Entries :    38579 : Total  Size=     155152 bytes  File Size  =     132155 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression=   1.17     *
    *............................................................................*
    *Br    6 :xspot     : xspot[2]/F                                             *
    *Entries :    38579 : Total  Size=     309863 bytes  File Size  =     287876 *
    *Baskets :       10 : Basket Size=      32000 bytes  Compression=   1.07     *
    *............................................................................*
    *Br    7 :ptype     : ptype/I                                                *
    *Entries :    38579 : Total  Size=     155161 bytes  File Size  =       1290 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression= 119.90     *
    *............................................................................*
    *Br    8 :det       : det/I                                                  *
    *Entries :    38579 : Total  Size=     155143 bytes  File Size  =       1280 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression= 120.83     *
    *............................................................................*
    *Br    9 :mint      : mint/I                                                 *
    *Entries :    38579 : Total  Size=     155152 bytes  File Size  =       1285 *
    *Baskets :        5 : Basket Size=      32000 bytes  Compression= 120.37     *
    *............................................................................*
    *Br   10 :xint      : xint[mint][3]/F                                        *
    *Entries :    38579 : Total  Size=     620133 bytes  File Size  =     408876 *
    *Baskets :       25 : Basket Size=      32000 bytes  Compression=   1.51     *
    *............................................................................*
    *Br   11 :tint      : tint[mint]/F                                           *
    *Entries :    38579 : Total  Size=     310505 bytes  File Size  =      95568 *
    *Baskets :       15 : Basket Size=      32000 bytes  Compression=   3.24     *
    *............................................................................*
    *Br   12 :pint      : pint[mint]/I                                           *
    *Entries :    38579 : Total  Size=     310498 bytes  File Size  =      49507 *
    *Baskets :       15 : Basket Size=      32000 bytes  Compression=   6.26     *
    *............................................................................*

## Look at the time structure of the photon beam

In [25]:
def det5_timing_hinit():
    h = {}
    h['htimeklong'] = ROOT.TH1D('htimeklong', "time of klongs at GlueX entrance plane", 10000, -100, 100)
    h['htimeklong'].GetXaxis().SetTitle("time (ns)")
    h['htimeklong'].GetYaxis().SetTitle("counts")
    h['htimegamma'] = ROOT.TH1D('htimegamma', "time of gammas at GlueX entrance plane", 10000, -100, 100)
    h['htimegamma'].GetXaxis().SetTitle("time (ns)")
    h['htimegamma'].GetYaxis().SetTitle("counts")
    h['htimeneutron'] = ROOT.TH1D('htimeneutron', "time of neutrons at GlueX entrance plane", 10000, -100, 100)
    h['htimeneutron'].GetXaxis().SetTitle("time (ns)")
    h['htimeneutron'].GetYaxis().SetTitle("counts")
    h['htimemuon'] = ROOT.TH1D('htimemuon', "time of muons at GlueX entrance plane", 10000, -100, 100)
    h['htimemuon'].GetXaxis().SetTitle("time (ns)")
    h['htimemuon'].GetYaxis().SetTitle("counts")
    return h

def det5_timing_hfill(row, histos):
    if row.ptype == 10 and row.x[5] > 0:
        histos['htimeklong'].Fill(row.time)
    elif row.ptype == 1 and row.x[5] > 0:
        histos['htimegamma'].Fill(row.time)
    elif row.ptype == 13 and row.x[5] > 0:
        histos['htimeneutron'].Fill(row.time)
    elif (row.ptype == 5 or row.ptype == 6) and row.x[5] > 0:
        histos['htimemuon'].Fill(row.time)
    return histos

n = tview.declare_histograms("det5 timing", det5_timing_hinit, det5_timing_hfill)

In [26]:
tview.fill_histograms()
n = tview.draw([['htimeklong', 'htimegamma'],
                ['htimeneutron', 'htimemuon']])

fill_histograms read a total of 2371 tree files, 69620272.0 records


In [27]:
def wrap64ns(hname, htime):
    htimewrap = htime.Clone(hname)
    for i in range(htime.GetNbinsX()):
        t = htime.GetXaxis().GetBinCenter(i+1)
        for dt in [-192, -128, -64, 64, 128, 192]:
            htimewrap.Fill(t + dt, htime.GetBinContent(i+1))
    return htimewrap

In [28]:
try:
    htgammawrap = tview.get("htgammawrap")
    htklongwrap = tview.get("htklongwrap")
    htneutwrap = tview.get("htneutwrap")
    htneutfold = tview.get("htneutfold")
    [h.SetStats(0) for h in (htgammawrap, htklongwrap, htneutwrap, htneutfold)]
    refresh = FalseX
except:
    refresh = True
    htgammawrap = wrap64ns("htgammawrap", tview.get('htimegamma'))
    htklongwrap = wrap64ns("htklongwrap", tview.get('htimeklong'))
    htneut = tview.get("htimeneutron")
    htneutfold = tview.get("htimeneutron").Clone("htneutfold")
    htneutfold.Reset()
    for i in range(htneut.GetNbinsX()):
        for n in range(int(htneut.GetBinContent(i+1))):
            t = htneut.GetXaxis().GetBinCenter(i+1) + (np.random.uniform() - 0.5) * htneut.GetXaxis().GetBinWidth(i+1)
            while t > 172:
                t -= 192
            htneutfold.Fill(t)
    htneutwrap = wrap64ns("htneutwrap", htneutfold)
    [h.SetStats(0) for h in (htgammawrap, htklongwrap, htneutwrap)]
htgammawrap.SetLineColor(2)
htneutwrap.SetLineColor(3)
htgammawrap.SetMaximum(1e7)
htgammawrap.SetMinimum(1)
htgammawrap.GetXaxis().SetTitle("time at GlueX entrance plane (ns)")
htgammawrap.GetYaxis().SetTitle("counts")
if refresh:
    [tview.put(h) for h in (htgammawrap, htklongwrap, htneutfold, htneutwrap)]
n = tview.draw([[['htgammawrap', 'htklongwrap', 'htneutwrap']]], [[['hist'*3]]], width=1000, titles=0)

In [29]:
tview.list_histograms(True)

hptypef;1       particle type at GlueX entrance plane           58377356   Sun Oct  6 07:03:13 2024
hklfspot;1      klong impact point at GlueX entrance plane             0   Sun Oct  6 07:03:13 2024
hklfspot2;1     klong impact point at GlueX entrance plane             0   Sun Oct  6 07:03:13 2024
hklftotE;1      klong total energy inside pipe at GlueX entrance plane          0   Sun Oct  6 07:03:13 2024
hklfmom;1       klong momentum inside pipe at GlueX entrance plane          0   Sun Oct  6 07:03:13 2024
hgamfspot;1     gamma impact point at GlueX entrance plane      58319524   Sun Oct  6 07:03:13 2024
hgamfspot2;1    gamma impact point at GlueX entrance plane      58319524   Sun Oct  6 07:03:13 2024
hgamftotE;1     gamma total energy inside pipe at GlueX entrance plane   58156059   Sun Oct  6 07:03:13 2024
hgamftotE0;1    gamma total energy inside pipe at GlueX entrance plane   58156059   Sun Oct  6 07:03:13 2024
hgamftotE1;1    gamma total energy inside pipe at GlueX entrance pla

80

In [30]:
n = tview.draw('fill_histograms_stats', width=1000)